# Notebook to experiment with topic model

# Imports

In [1]:
### Local functions
import topic_model

### Libraries
import os
import re
import string

## Spacy
import spacy
spacy.load('en')
from spacy.lang.en import English
parser = English()

## nltk
import nltk
nltk.download('wordnet')
nltk.download('stopwords')
en_stop = set(nltk.corpus.stopwords.words('english'))

[nltk_data] Downloading package wordnet to /Users/ellen/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to /Users/ellen/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/ellen/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to /Users/ellen/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


# Part 1 Load PDFs from folder 'papers'

In [2]:
def get_file_names(folder='papers'):
    """
    
    :param folder: string, name of folder where the papers are contained
    :return: string foldername, list filenames
    """
    if not os.path.exists(folder):
        os.makedirs(folder)
    file_names = os.listdir(folder)
    return folder, file_names


foldername, filenames = get_file_names('papers')

filenames


['00_manuscript-complete.pdf',
 'Hybrid Recommender Systems.pdf',
 'Information Theory - Tutorial.pdf',
 'Geometric Understanding of Deep Learning.pdf',
 '1802.05968v2.pdf',
 'Time Series Feature Extraction.pdf',
 'An Introduction to DRL.pdf',
 'Multitask Learning as Multiobjective Optimization.pdf',
 'GANs.pdf',
 'Introduction to Transfer Learning.pdf',
 'Deep CNN Design Patterns.pdf']

# Part 2 Retrieve the text from the PDF files

We use pdf miner to retrieve the text from the filenames in our 'papers' folder

In [3]:
from pdfminer.pdfinterp import PDFResourceManager, PDFPageInterpreter
from pdfminer.pdfpage import PDFPage
from pdfminer.converter import XMLConverter, TextConverter
from pdfminer.layout import LAParams
import io

# TODO check if this works for multiple papers too
# TODO e.g. is it possible to create a list of tokens for each? 
# TODO what is the best way to do this?
# TODO is this already sth that should be returned in the end?


def pdfparser(filename):
    """
    
    :param data: filename (string)
    :return: text data (string), the complete text in the document(s)
    """
    fp = open(filename, 'rb')
    rsrcmgr = PDFResourceManager()
    retstr = io.StringIO()
    codec = 'utf-8'
    laparams = LAParams()
    device = TextConverter(rsrcmgr, retstr, codec=codec, laparams=laparams)
    # Create a PDF interpreter object.
    interpreter = PDFPageInterpreter(rsrcmgr, device)
    # Process each page contained in the document.

    for page in PDFPage.get_pages(fp):
        interpreter.process_page(page)
        data = retstr.getvalue()
    return data


In [15]:
text = []

for each in range(len(filenames)):
    text.append(pdfparser(foldername+'/'+filenames[each]))
    
len(text)

11

In [16]:
len(text[0])

420075

In [19]:
# each = pdfparser(foldername+'/'+filenames[0])  # example, just for the first paper

# TODO cleansing operations directly on raw each
for each in text:
    each= each.replace("\n"," ")
    each = re.sub(r'\d+', '', each)
    each = each.translate(str.maketrans("","", string.punctuation))
    each = each.strip()
    # each = each.strip("\r\n")
    each = re.sub(r'\b\w{1,3}\b', '', each)
    # each = [tok for tok in each if tok not in STOPLIST and tok not in punctuations]
    # each = ' '.join(each)

In [20]:
text[0:600]

['Supervised Machine Learning in Smart Service\nSystems: Uncover Holistic Insights in Distributed\nData\n\nRobin Lothar Hirt\n\nxx. xxxx, 2019\nVersion: v01\n\n\x0c\x0cSupervised Machine Learning in Smart Service\n\nSystems: Uncover Holistic Insights in\n\nDistributed Data\n\nZur Erlangung des akademischen Grades eines\n\nDoktors der Ingenieurwissenschaften\n\n(Dr.-Ing.)\n\nvon der Fakultät der Wirtschaftswissenschaften\n\ndes Karlsruher Instituts für Technologie\n\neingereichte\n\nDissertation\n\nvon\n\nRobin Lothar Hirt\n\n1. Gutachter\n\nProf. Dr. Gerhard Satzger\n\nxx. xxxx, 2019\n\n\x0cRobin Lothar Hirt\nSupervised Machine Learning in Smart Service Systems: Uncover Holistic Insights in Distributed\nData\nDissertation, xx. xxxx, 2019\nGutachter: Prof. Dr. Gerhard Satzger und Prof. Dr. Ali Sunayev\nKarlsruhe Institute of Technology\nKarlsruhe Service Research Institute\nFaculty of Economics\nKaiserstr. 89\n76131 and Karlsruhe\n\n\x0cAbstract\n\nOne of the key drivers for a companys 

# Part 3 Quick data exploration: check of top x words with nltk freqdist

In [28]:
all_tokens = []
for each in range(len(text)):
    all_tokens.append(topic_model.prepare_text_for_lda(text[each]))

In [31]:
len(all_tokens)

11

In [43]:
# Calculate frequency distribution
dict_object = []
for each in all_tokens:
    fdist = nltk.FreqDist(each)
    # Output top 20 words
    word_list = []
    frequency_list = []
    for word, frequency in fdist.most_common(10):
        word_list.append(word)
        frequency_list.append(frequency)
    frequency_dict = dict(zip(word_list, frequency_list))
    dict_object.append(frequency_dict)
        # print(u'{};{}'.format(word, frequency))
    # print('\n')



In [66]:
def print_dict_object(dct, paper_title):
    print("Top 10 words for paper {}:".format(paper_title))
    for item, amount in dct.items():
        print("{} : ({})".format(item, amount))

In [67]:
print_dict_object(dict_object[1], filenames[0])

Top 10 words for paper Hybrid Recommender Systems.pdf:
hybrid : (192)
system : (184)
recommendation : (167)
study : (152)
recommender : (123)
base : (101)
author : (78)
technique : (75)
problem : (68)
domain : (67)


In [50]:
def mutual_words(**lists):
    return list(set(**lists))

In [51]:
mutual_words(dict_object)

TypeError: type object argument after ** must be a mapping, not tuple

In [ ]:
# Wordclouds


# Part 4 Preprocessing: remove punctuation, newline chars, stopwords etc

In [8]:
nlp = spacy.load('en_core_web_sm')

# text is a string of all the separate tokens
print("The paper contains " + str(len(text)) + " tokens in total")
print("Here are the tokens at position 400-420: \n\n '" + str(text[400:420]) + " ' \n")

# create spacy tokens
tokens = nlp(text)
print("After conversion to " + str(type(tokens)) + " the paper contains " + str(len(tokens)) + " tokens")
print("Here are the tokens at position 400-420:  \n\n'" + str(tokens[400:420]) + "'")

The paper contains 340809 tokens in total
Here are the tokens at position 400-420: 

 ' Dissertation    Rob ' 

After conversion to <class 'spacy.tokens.doc.Doc'> the paper contains 54765 tokens
Here are the tokens at position 400-420:  

'data under organizational constraints  smart service systems  contributes   body  knowledge  proposing methods  data analyses'


## 4a) Remove stopwords and punctuations

In [9]:
from nltk.corpus import stopwords
STOPLIST = set(stopwords.words('english'))
SYMBOLS = " ".join(string.punctuation).split(" ") + ["-", "...", "”", "”"]
punctuations = string.punctuation


def clean_up(tokens):
    clean_tokens = []
    for each in tokens:
        if each.is_stop == False:
            if each.is_punct == False:
                clean_tokens.append(each)
    final_tokens = [tok.lemma_.lower().strip() for tok in clean_tokens if tok.lemma_ != '-PRON-']
    final_tokens = [tok for tok in final_tokens if tok not in STOPLIST and tok not in punctuations]
    final_tokens = ' '.join(final_tokens)
    return final_tokens

def further_clean_up(tokens):
    tokens = re.sub(r'\d+', '', tokens)
    tokens = tokens.translate(str.maketrans("","", string.punctuation))
    tokens = tokens.strip()
    tokens = re.sub(r'\b\w{1,3}\b', '', tokens)
    return tokens


# apply the clean_up functions to the spacy nlp tokens
clean_tokens = clean_up(tokens)
clean_tokens = further_clean_up(clean_tokens)
clean_tokens = clean_tokens.strip()
clean_tokens[400:800]


't gutachter prof gerhard satzger xxxx robin lothar hirt supervised machine learning smart service systems uncover holistic insights distributed data dissertation xxxx gutachter prof gerhard satzger prof sunayev karlsruhe institute technology karlsruhe service research institute faculty economics kaiserstr karlsruhe abstract driver company success capability well cision analysis datum supervised ma'

In [10]:
# unfortunately this returns a string again so we need to apply nlp again 

final_tokens = nlp(clean_tokens)
final_tokens[400:600]

methodology outlook references enable interorganizational analytics business networks meta machine learning introduction foundations methodology business networks meta machine learning research design relate work preserving data conﬁdentiality reduce process large data streams concept interorganizational meta machine learning architecture data model output exchange analysis life cycle meta machine learning method evaluation discussion viii case artifact instantiation preserving data conﬁdentiality reduction transferred data volume performance method conclusion cognitive computing customer proﬁling meta classiﬁcation gender prediction introduction research design related work contribution theory cognitive approach customer classiﬁcation meta chine learning development artifact gender detection twitter data data tweetbased classiﬁcation namebased classiﬁcation imagebased classiﬁcation combining predictions meta classiﬁcation deployment artifact service evaluation technical experiment ill

## 4b) POS tagging

In [11]:
# for token in doc:
#     print(token.text, token.lemma_, token.pos_, token.tag_, token.dep_,
#             token.shape_, token.is_alpha, token.is_stop)

for token in final_tokens:
    # print(token.pos_)
    pass

for word in final_tokens[300:330]:  
    print(word.text,  word.pos_)

for noun in final_tokens[300:330].noun_chunks:  
    # print(noun.text)
    pass

uniﬁed ADJ
terminology NOUN
introduction NOUN
theoretical ADJ
foundations NOUN
sociotechnical ADJ
systems NOUN
systemsofsystems VERB
methodology NOUN
results NOUN
service NOUN
systems NOUN
smart ADJ
service NOUN
systems NOUN
cyberphysical ADJ
systems NOUN
summary NOUN
discussion NOUN
conclusion NOUN
references NOUN
endtoend VERB
process NOUN
model NOUN
supervised VERB
machine NOUN
learning VERB
clas ADJ
siﬁcation NOUN
problem NOUN


## 4c) Lemmatization

Now that we are finished with the data cleaning, we can apply lemmatization to the final tokens

Lemmatization is sufficient for our use case, we do not apply stemming

In [12]:
# TODO remove empty values

def lemmatizer(tokens):
    spacy_lemmas = []
    for word in tokens:
        spacy_lemmas.append(word.lemma_)
    return spacy_lemmas
 
   
lemmatized_tokens = lemmatizer(final_tokens)

print(lemmatized_tokens[600:800])

['available', 'datum', 'grow', 'vastly', 'business', 'perspective', 'datum', 'create', 'value', 'order', 'company', 'stay', 'competitive', 'analyze', 'accumulate', 'pile', 'datum', 'derive', 'insight', 'michael', 'porter', 'heppelmann', 'opresnik', 'taisch', 'lavalle', 'less', 'shockley', 'hopkin', 'kruschwitz', 'thomas', 'davenport', 'decade', 'machine', 'learning', 'emerge', 'main', 'driver', 'analyze', 'seemingly', 'random', 'evergrowe', 'datum', 'jordan', 'mitchell', 'machine', 'learn', 'ﬁeld', 'study', 'give', 'put', 'ability', 'learn', 'datum', 'explicitly', 'program', 'samuel', 'koza', 'bennett', 'andre', 'keane', 'general', 'machine', 'learn', 'divide', 'unsupervised', 'reinforcement', 'supervise', 'machine', 'learn', 'unsu', 'pervise', 'machine', 'learn', 'comprise', 'method', 'algorithm', 'reveal', 'previously', 'unknown', 'pattern', 'datum', 'consequently', 'unsupervised', 'learn', 'task', 'essarily', 'correct', 'solution', 'ground', 'truth', 'wang', 'wang', 'peng', 'reinfor

In [263]:
# from nltk.stem.snowball import SnowballStemmer
# 
# stemmer = SnowballStemmer(language='english')
# 
# # test_tokens = ['compute', 'computer', 'computed', 'computing']
# # document = sp(spacy_tokens[200:300])
# id_sequence = map(lam'bda x: x.orth, [token for token in spacy_tokens[200:300]])
# text = map(lambda x: sp.vocab[x].text, [id for id in id_sequence])
# 
# for token in text:  
#     print(token + ' --> ' + stemmer.stem(token))

# 5) Analyze ngrams

In [14]:
import nltk
from nltk.util import ngrams

def word_grams(words, number):
    s = []
    for ngram in ngrams(words, number):
            s.append(' '.join(str(i) for i in ngram))
    return s

In [15]:
bigrams = word_grams(lemmatized_tokens, 2)
from collections import Counter
count_grams = Counter(bigrams)
count_grams.most_common(20)

[('service system', 312),
 ('machine learn', 265),
 ('smart service', 227),
 ('supervise machine', 133),
 ('machine learning', 133),
 ('business network', 112),
 ('meta machine', 106),
 ('distribute datum', 95),
 ('information system', 91),
 ('datum source', 79),
 ('process model', 55),
 ('meta model', 52),
 ('datum conﬁdentiality', 48),
 ('meta classiﬁer', 47),
 ('meta unit', 43),
 ('transfer machine', 42),
 ('cyberphysical system', 42),
 ('learning model', 40),
 ('include publication', 39),
 ('research question', 38)]

# 6) Creating a model to compare similarities of documents

In [266]:
# Start with LDA and Jensen-Shannon distance
# And Glove with Cosine Similarity


In [267]:
# lemma_tokens = nlp(str(lemmatized_tokens))
# lemma_tokens.join(' ')

In [237]:
# lemma_tokens

In [16]:
# TODO why are there so many ' and , here in lemma_tokens?
# TODO clean
for token in final_tokens[1000:1020]:
    print(token.text, token.has_vector, token.vector_norm, token.is_oov)

datum True 22.305706 True
component True 25.578114 True
distribute True 23.91271 True
smart True 25.785675 True
service True 26.756544 True
system True 27.381582 True
example True 27.263954 True
information True 27.454609 True
component True 23.663631 True
customer True 26.383387 True
insurance True 24.582508 True
company True 26.604555 True
insurance True 25.011106 True
company True 26.405184 True
possession True 25.515772 True
essential True 24.71286 True
information True 27.797071 True
customer True 26.849031 True
address True 26.391354 True
relevant True 25.636343 True


In [255]:
# for token1 in final_tokens:
# for token2 in final_tokens[400:500]:
#         print(token1.similarity(token2))
    

/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Token.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add your own word vectors, or use one of the larger models instead if available.
  "__main__", mod_spec)
/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Token.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add y

0.31558728
0.35222763
0.5915981
0.36502123
0.0687297
0.4382803
0.56497437
0.35251856
0.39734998
0.38165852
0.30290228
0.4261979
0.4900853
0.25588998
0.44724917
0.41276097
0.3599466
0.20822087
0.11901125
0.55339766
0.4151353
0.39335424
0.38373357
0.4372713


/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Token.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add your own word vectors, or use one of the larger models instead if available.
  "__main__", mod_spec)
/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Token.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add y

0.31960154
0.42925134
0.5426847
0.39630258
0.19520226
0.040165655
0.5284617
0.38723338
0.29347414
0.3591757
0.48219705
0.34044817
0.5949429
0.28052828
0.18128164
0.36459067
0.33198982
0.19759299
0.4412117
0.42851982
0.4533855
0.36772022
0.32539573
0.004794926


/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Token.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add your own word vectors, or use one of the larger models instead if available.
  "__main__", mod_spec)
/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Token.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add y

...

/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Token.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add your own word vectors, or use one of the larger models instead if available.
  "__main__", mod_spec)
/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Token.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add y

0.47914505
-0.0059779175
0.40651846
0.45974436
0.47421032
0.22479178
0.49491698
0.42146403
0.40953496
0.7245297
0.34126815
0.375349
0.5924127
0.6387903
0.72393566
0.70777476
0.5158093
0.67309123
0.7527208
0.3940823
0.2592641
0.45393708
0.18160611
0.34583277
0.17830086
0.63977367
0.63178456
0.64305925
0.6898694
0.6213077
0.51843375
0.6209602


/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Token.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add your own word vectors, or use one of the larger models instead if available.
  "__main__", mod_spec)
/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Token.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add y

0.6241606
0.5639367
Traceback (most recent call last):
  File "/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/site-packages/IPython/core/interactiveshell.py", line 3296, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-255-4e7f232a8bc0>", line 3, in <module>
    print(token1.similarity(token2))
  File "token.pyx", line 213, in spacy.tokens.token.Token.similarity
  File "/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/site-packages/spacy/errors.py", line 445, in models_warning
    _warn(message, "models")
  File "/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/site-packages/spacy/errors.py", line 460, in _warn
    stack = inspect.stack()[-1]
  File "/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/inspect.py", line 1499, in stack
    return getouterframes(sys._getframe(1), context)
  File "/Users/ellen/anaconda3/envs/pnet36/lib/python3.6/inspect.py", line 1476, in getouterframes
    frameinfo = (frame,) + getframeinfo(frame, context)
  File "/

KeyboardInterrupt: 

In [17]:
from sklearn.decomposition import NMF, LatentDirichletAllocation, TruncatedSVD
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.manifold import TSNE



# Creating a vectorizer
vectorizer = CountVectorizer(min_df=5, max_df=0.9, stop_words='english', lowercase=True, token_pattern='[a-zA-Z\-][a-zA-Z\-]{2,}')
data_vectorized = vectorizer.fit_transform(lemmatized_tokens)

In [18]:
NUM_TOPICS = 3


In [19]:
# Latent Dirichlet Allocation Model
lda = LatentDirichletAllocation(n_components=NUM_TOPICS, max_iter=5, learning_method='online',verbose=True)
data_lda = lda.fit_transform(data_vectorized)

iteration: 1 of max_iter: 5
iteration: 2 of max_iter: 5
iteration: 3 of max_iter: 5
iteration: 4 of max_iter: 5
iteration: 5 of max_iter: 5


In [20]:
# Non-Negative Matrix Factorization Model
nmf = NMF(n_components=NUM_TOPICS)
data_nmf = nmf.fit_transform(data_vectorized) 


In [21]:
# Latent Semantic Indexing Model using Truncated SVD
lsi = TruncatedSVD(n_components=NUM_TOPICS)
data_lsi = lsi.fit_transform(data_vectorized)

In [22]:
# Functions for printing keywords for each topic
def selected_topics(model, vectorizer, top_n=10):
    for idx, topic in enumerate(model.components_):
        print("Topic %d:" % (idx))
        print([(vectorizer.get_feature_names()[i], topic[i])
                        for i in topic.argsort()[:-top_n - 1:-1]]) 

In [23]:
# Keywords for topics clustered by Latent Dirichlet Allocation
print("LDA Model:")
selected_topics(lda, vectorizer)

LDA Model:
Topic 0:
[('learn', 439.4769989950086), ('classi', 431.694604974079), ('meta', 382.29074761303804), ('method', 220.74811192863717), ('different', 200.01534614961616), ('work', 173.96250385973835), ('analysis', 161.52183563458306), ('cation', 147.6112446045492), ('design', 139.69764506491134), ('supervise', 136.2291967059247)]
Topic 1:
[('datum', 1015.8678254483225), ('model', 468.5701869869336), ('service', 398.3504088852606), ('research', 245.89019259973966), ('smart', 183.36542223966796), ('analytic', 167.26275522751828), ('prediction', 161.31446486733188), ('learning', 152.98637941665396), ('distribute', 152.0438755778839), ('cognitive', 144.2406489669578)]
Topic 2:
[('machine', 405.46824894430955), ('transfer', 307.39302792504776), ('information', 245.738401824508), ('network', 215.86417853731487), ('base', 214.97424227661878), ('business', 208.10196416301736), ('process', 167.38382820455598), ('performance', 145.21558960852585), ('unit', 133.62487062661367), ('source', 

In [24]:
# Keywords for topics clustered by Latent Semantic Indexing
print("NMF Model:")
selected_topics(nmf, vectorizer)

NMF Model:
Topic 0:
[('datum', 5.642992703887905), ('information', 1.8353310203815174e-41), ('method', 1.318293153359291e-43), ('analytic', 1.1272191932762779e-46), ('business', 5.387636789332615e-47), ('work', 1.473253061751156e-49), ('evaluate', 0.0), ('estimate', 0.0), ('estimation', 0.0), ('estimator', 0.0)]
Topic 1:
[('service', 4.719220244170946), ('classi', 3.266345151558138e-07), ('cation', 1.4136455870831617e-07), ('identi', 6.579752792899669e-10), ('transfer', 5.2753724053041267e-20), ('method', 1.1927506504124538e-23), ('base', 9.502553519822248e-24), ('analytic', 1.229658538761844e-26), ('process', 3.332010578449691e-27), ('network', 1.3554148645532857e-27)]
Topic 2:
[('model', 4.638663254426569), ('learn', 1.477023640217535e-05), ('machine', 1.4915568736876156e-07), ('information', 6.982943024600552e-19), ('base', 9.403883315124632e-23), ('different', 3.016707875321354e-23), ('cognitive', 1.181447828244441e-28), ('supervise', 8.642042834658391e-33), ('source', 1.2589511064

In [25]:
# Keywords for topics clustered by Non-Negative Matrix Factorization
print("LSI Model:")
selected_topics(lsi, vectorizer)

LSI Model:
Topic 0:
[('datum', 0.9999999950609616), ('different', 6.414785790457982e-05), ('business', 2.139741432562939e-05), ('research', 1.3380799622054211e-05), ('prediction', 1.0781189069551037e-05), ('analysis', 5.891200717468752e-06), ('smart', 4.6987785490178044e-06), ('unit', 4.1138499411107836e-06), ('performance', 3.649219240669831e-06), ('work', 3.261941214431393e-06)]
Topic 1:
[('service', 0.999981484874632), ('analytic', 0.003438243518440558), ('different', 0.0026224643398489395), ('cognitive', 0.0012164596682615605), ('method', 0.0009295067783487456), ('research', 0.0005533623951320825), ('meta', 0.0002960523111401152), ('user', 0.00011653188849817645), ('concept', 8.277684698548147e-05), ('knowledge', 8.104354187070189e-05)]
Topic 2:
[('model', 0.9999638684941159), ('different', 0.003395157694088054), ('work', 0.0016708187303302842), ('classi', 0.001609614002266949), ('smart', 0.0011556764156581826), ('business', 0.0010966731092975491), ('prediction', 0.0007914160988274